# torchtext 라이브러리를 이용하여 IMDB 데이터셋 준비하기

torchtext 라이브러리를 이용하면 IMDB 데이터셋을 다운로드 할 수 있다.

# torchtext.data

torchtext.data 인스턴스에는 Field라는 클래스가 정의돼 있다.

Field 클래스는 데이터를 읽거나 토큰화하는 방법을 정의하는데 유용하다.

Field 클래스의 생성자는 tokenize라는 인자를 갖는데 이 인자의 기본값은 str.split이다.

이 인자에 spaCy나 다른 토크나이저를 설정할 수 있다!

In [13]:
from torchtext import data

TEXT = data.Field(lower=True, batch_first=True, fix_length=40) 
# 모든 텍스트를 소문자로 만들고 배치 형태로 처리하고 총 텍스트의 길이는 40이다.
LABEL = data.Field(sequential=False)
# 데이터 타입이 Sequential한 형태를 갖도록 한다.

# torchtext.datasets

torchtext.datasets은 IMDB, TREC 등의 다른 여러 데이터셋을 사용하기 위한 래퍼 클래스를 제공한다.

torch.datasets를 사용해 다음 코드와 같이 IMDB 데이터셋을 다운로드하고, 이 데이터셋을 학습 데이터셋과 테스트 데이터셋으로 나눌 수 있다.

In [14]:
from torchtext import datasets

train, test = datasets.IMDB.splits(TEXT, LABEL) # 현재 프로젝트 폴더에 .data 폴더를 만들고 데이터셋을 그 곳에 다운로드한다.
# 이미 다운로드를 받았다면 다음번에 코드를 실행할 때 다시 다운 받지 않는다.

위의 코드에서 datasets의 IMDB 클래스는 데이터셋을 다운로드하고

토큰화를 수행한 다음에 이 데이터셋을 학습 데이터셋과 테스트 데이터셋으로 분할하는 데 필요한 복잡한 작업을 추상화한다.

In [15]:
print(train.fields)

{'text': <torchtext.data.field.Field object at 0x00000156FF67D8B0>, 'label': <torchtext.data.field.Field object at 0x00000156FF67D490>}


In [16]:
print(vars(train[0])) # vars() 내장함수 : 객체를 Dictionary 형태로 만들어 반환하는 함수임

{'text': ['bromwell', 'high', 'is', 'a', 'cartoon', 'comedy.', 'it', 'ran', 'at', 'the', 'same', 'time', 'as', 'some', 'other', 'programs', 'about', 'school', 'life,', 'such', 'as', '"teachers".', 'my', '35', 'years', 'in', 'the', 'teaching', 'profession', 'lead', 'me', 'to', 'believe', 'that', 'bromwell', "high's", 'satire', 'is', 'much', 'closer', 'to', 'reality', 'than', 'is', '"teachers".', 'the', 'scramble', 'to', 'survive', 'financially,', 'the', 'insightful', 'students', 'who', 'can', 'see', 'right', 'through', 'their', 'pathetic', "teachers'", 'pomp,', 'the', 'pettiness', 'of', 'the', 'whole', 'situation,', 'all', 'remind', 'me', 'of', 'the', 'schools', 'i', 'knew', 'and', 'their', 'students.', 'when', 'i', 'saw', 'the', 'episode', 'in', 'which', 'a', 'student', 'repeatedly', 'tried', 'to', 'burn', 'down', 'the', 'school,', 'i', 'immediately', 'recalled', '.........', 'at', '..........', 'high.', 'a', 'classic', 'line:', 'inspector:', "i'm", 'here', 'to', 'sack', 'one', 'of', '

### 잠시, vars() 내장 함수에 대해 알아보고 가자.

vars() 함수는 객체들의 필드 변수들을 Dictionary 형태로 만들어서 반환해주는 함수이다.

다음의 코드를 통해 동작과정을 익히도록 하자.

In [17]:
class sehun():
    def __init__(self):
        self.a = 0
        self.b = 1

hi = sehun()

In [18]:
print(hi)

In [19]:
print(vars(hi))

{'a': 0, 'b': 1}


# Vocab 구축하기

torchtext는 vocab을 더 쉽게 만드는 기능을 제공한다.

build_vocab() 함수를 사용하면 된다.

아래의 코드를 사용하면 어휘 객체를 생성하는 부분에 train 객체를 전달하고,

사전에 학습된 300차원의 임베딩을 이용하여 벡터를 초기화하도록 하고 있다.

또한, max_size 속성으로 생성될 어휘 객체의 크기를 제한하고,

min_freq 속성으로 어휘에 추가될 단어의 최소 출현 빈도를 설정한다.

이를 통해 아래의 코드에서는 출현 빈도가 10번 이상인 단어로 최대 크기가 1만 개인 어휘 객체가 만들어진다.

In [20]:
from torchtext.vocab import GloVe

TEXT.build_vocab(train, vectors=GloVe(name='6B', dim=300), max_size=10000, min_freq=10)
LABEL.build_vocab(train)

vocab이 만들어지면, vocab으로부터 각 단어의 출현 빈도, 단어 인덱스 및 단어의 벡터 표현과 같은 여러 가지 값을 얻을 수 있다.

In [21]:
print(TEXT.vocab.freqs)

Counter({'the': 322198, 'a': 159953, 'and': 158572, 'of': 144462, 'to': 133967, 'is': 104171, 'in': 90527, 'i': 70480, 'this': 69714, 'that': 66292, 'it': 65505, '/><br': 50935, 'was': 47024, 'as': 45102, 'for': 42843, 'with': 42729, 'but': 39764, 'on': 31619, 'movie': 30887, 'his': 29059, 'are': 28743, 'not': 28597, 'film': 27777, 'you': 27564, 'have': 27344, 'he': 26177, 'be': 25691, 'at': 22731, 'one': 22480, 'by': 21976, 'an': 21240, 'they': 20624, 'from': 19934, 'all': 19740, 'who': 19407, 'like': 18779, 'so': 18099, 'just': 17309, 'or': 16769, 'has': 16570, 'her': 16540, 'about': 16486, "it's": 15970, 'some': 15280, 'if': 15189, 'out': 14510, 'what': 14055, 'very': 13633, 'when': 13609, 'more': 13170, 'there': 13094, 'she': 12234, 'would': 12027, 'even': 12010, 'good': 11926, 'my': 11766, 'only': 11566, 'their': 11317, 'no': 11273, 'really': 11065, 'had': 11042, 'which': 10898, 'can': 10797, 'up': 10776, 'were': 10528, 'see': 10410, 'than': 9807, 'we': 9417, '-': 9355, 'been': 90

In [22]:
print(TEXT.vocab.vectors)

tensor([[ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.0466,  0.2132, -0.0074,  ...,  0.0091, -0.2099,  0.0539],
        ...,
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000],
        [ 0.7724, -0.1800,  0.2072,  ...,  0.6736,  0.2263, -0.2919],
        [ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0000]])


In [23]:
print(TEXT.vocab.stoi) # vocab의 stoi 속성을 통해 각 단어의 인덱스를 알 수 있음

defaultdict(<bound method Vocab._default_unk_index of <torchtext.vocab.Vocab object at 0x00000156F9CD2AF0>>, {'<unk>': 0, '<pad>': 1, 'the': 2, 'a': 3, 'and': 4, 'of': 5, 'to': 6, 'is': 7, 'in': 8, 'i': 9, 'this': 10, 'that': 11, 'it': 12, '/><br': 13, 'was': 14, 'as': 15, 'for': 16, 'with': 17, 'but': 18, 'on': 19, 'movie': 20, 'his': 21, 'are': 22, 'not': 23, 'film': 24, 'you': 25, 'have': 26, 'he': 27, 'be': 28, 'at': 29, 'one': 30, 'by': 31, 'an': 32, 'they': 33, 'from': 34, 'all': 35, 'who': 36, 'like': 37, 'so': 38, 'just': 39, 'or': 40, 'has': 41, 'her': 42, 'about': 43, "it's": 44, 'some': 45, 'if': 46, 'out': 47, 'what': 48, 'very': 49, 'when': 50, 'more': 51, 'there': 52, 'she': 53, 'would': 54, 'even': 55, 'good': 56, 'my': 57, 'only': 58, 'their': 59, 'no': 60, 'really': 61, 'had': 62, 'which': 63, 'can': 64, 'up': 65, 'were': 66, 'see': 67, 'than': 68, 'we': 69, '-': 70, 'been': 71, 'into': 72, 'get': 73, 'will': 74, 'story': 75, 'much': 76, 'because': 77, 'most': 78, 'how

# 벡터 배치 생성

torchtext는 배치 처리를 지원하고 단어를 인덱스 번호로 대체하기 위해 BucketIterator를 제공한다.

BucketIterator는 batch_size, device, shuffle과 같은 인자를 가진다.

batch_size는 배치 크기를 의미하고 device는 CPU인지, GPU인지를 나타내고 shuffle은 데이터를 섞을 것인지 여부를 지정할 수 있게 해준다.

In [36]:
train_iter, test_iter = data.BucketIterator.splits( (train, test), batch_size=32, device=-1, shuffle=True)
# device = -1은 cpu를 의미한다. device의 default 값은 GPU이다.

The `device` argument should be set by using `torch.device` or passing a string as an argument. This behavior will be deprecated soon and currently defaults to cpu.
The `device` argument should be set by using `torch.device` or passing a string as an argument. This behavior will be deprecated soon and currently defaults to cpu.


다음 코드는 배치를 생성하는 방법과 배치에 포함된 데이터를 확인하는 방법에 대한 코드이다.

In [37]:
batch = next(iter(train_iter))

In [38]:
print(batch.text)

tensor([[   6,   28, 3399,  ..., 6366,  174,    6],
        [  10,    7,   23,  ...,  221,    6,    0],
        [   3, 1083,   16,  ...,   23,    2, 1735],
        ...,
        [7543, 2616,  272,  ...,  176,   21, 3657],
        [   9,  200,   10,  ...,    0,   10,   20],
        [  82,    5,  364,  ..., 1677,   66,    0]])


In [39]:
print(batch.label)

tensor([2, 2, 1, 1, 1, 2, 1, 2, 2, 2, 2, 2, 1, 1, 1, 1, 1, 2, 1, 2, 1, 2, 2, 2,
        1, 2, 1, 1, 1, 1, 2, 1])


In [40]:
print(batch.text.shape) # 행렬의 크기는 배치와 텍스트의 고정 길이이므로 128 x 40이다.

torch.Size([32, 40])


# 임베딩으로 네트워크 모델 만들기

In [67]:
import torch.nn as nn
import torch.nn.functional as F

class EmbNet(nn.Module):
    def __init__(self, emb_size, hidden_size1, hidden_size2=400):
        super().__init__()
        self.embedding = nn.Embedding(emb_size, hidden_size1)
        self.fc = nn.Linear(hidden_size2, 3)
    
    def forward(self, x):
        embeds = self.embedding(x).view(x.size(0), -1)
        out = self.fc(embeds)
        return F.log_softmax(out, dim=-1)

위의 코드에서 EmbNet은 임베딩을 한 다음에 선형 레이어를 통해 감성을 분류해주는 모델이다.

EmbNet은 첫 번째 인자로 vocab의 크기를 받고, 두 번째 인자(hidden_size1)로 각 단어를 표현하는 차원의 크기를 인자로 받는다.

고유한 단어의 수를 제한했으므로 어휘 크기는 10000이 될 것이고 워드 임베딩의 차원 크기는 10으로 시작할 수 있다.(아래의 코드에서 hidden_size=10으로 설정함으로써 워드 임베딩의 차원 크기를 지정해줌.)

워드 임베딩의 차원 크기는 학습 단계에서 사용자가 정해주는 것이다.

또한, 프로그램을 빨리 실행하려면 임베딩 크기가 작은 것이 유용하지만

프로덕션 시스템용 애플리케이션을 빌드할 때는 큰 크기의 임베딩을 사용해야 한다.

모델의 마지막에는 워드 임베딩을 3개의 카테고리에 대응시키는 선형 레이어가 사용된다.

------------------------------------

다음으로 forward 함수는 입력 데이터가 처리되는 방법을 정의한다.

만약 배치 크기가 32이고 최대 단어 길이가 40인 문장의 경우, 입력 데이터의 형상은 32 x 40이 된다.

또한 워드 임베딩이 10차원으로 만들어질 때, 단어를 워드 임베딩으로 교체하면 데이터 형상은 32 X 40 X 10이 된다.

이 형상을 문장별로 차원을 평평하게 만들기 위해 view() 함수를 사용한다.

위 예제의 경우, 다른 배치와 결합하지 않기 때문에 첫 번째 차원을 그대로 유지하고 나머지 값을 하나의 텐서로 합친다.

함수를 적용하면 출력 데이터 형상은 (32, 400)으로 변환된다.

마지막으로 이렇게 만들어진 임베딩의 출력을 Linear 레이어에 입력하면 된다.

In [68]:
model = EmbNet(len(TEXT.vocab.stoi),10)
model = model.cuda()

In [69]:
from torch import optim

optimizer = optim.Adam(model.parameters(),lr=0.001)

# 모델 학습시키기

In [70]:
train_iter.repeat = False
test_iter.repeat = False

In [71]:
import torch

def fit(epoch,model,data_loader,phase='training',volatile=False):
    if phase == 'training':
        model.train()
    if phase == 'validation':
        model.eval()
        volatile=True
    running_loss = 0.0
    running_correct = 0
    for batch_idx , batch in enumerate(data_loader):
        text , target = batch.text , batch.label
        if torch.cuda.is_available():
            text,target = text.cuda(),target.cuda()
        
        if phase == 'training':
            optimizer.zero_grad()
        output = model(text)
        loss = F.nll_loss(output,target)
        
        running_loss += F.nll_loss(output,target,size_average=False).data
        preds = output.data.max(dim=1,keepdim=True)[1]
        running_correct += preds.eq(target.data.view_as(preds)).cpu().sum()
        if phase == 'training':
            loss.backward()
            optimizer.step()
    
    loss = running_loss/len(data_loader.dataset)
    accuracy = 100. * running_correct.item()/len(data_loader.dataset)
    
    print(f'{phase} loss is {loss:{5}.{2}} and {phase} accuracy is {running_correct}/{len(data_loader.dataset)}{accuracy:{10}.{4}}')
    return loss,accuracy

In [72]:
train_losses , train_accuracy = [],[]
val_losses , val_accuracy = [],[]

In [73]:
%%time

for epoch in range(1,10):

    epoch_loss, epoch_accuracy = fit(epoch,model,train_iter,phase='training')
    val_epoch_loss , val_epoch_accuracy = fit(epoch,model,test_iter,phase='validation')
    train_losses.append(epoch_loss)
    train_accuracy.append(epoch_accuracy)
    val_losses.append(val_epoch_loss)
    val_accuracy.append(val_epoch_accuracy)

C:\Users\tpgns\anaconda3\envs\nlp_base\lib\site-packages\torch\nn\_reduction.py:43: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


training loss is  0.74 and training accuracy is 12918/25000     51.67
validation loss is  0.71 and validation accuracy is 13356/25000     53.42
training loss is  0.69 and training accuracy is 14303/25000     57.21
validation loss is  0.69 and validation accuracy is 14381/25000     57.52
training loss is  0.65 and training accuracy is 15676/25000      62.7
validation loss is  0.66 and validation accuracy is 15603/25000     62.41
training loss is   0.6 and training accuracy is 16845/25000     67.38
validation loss is  0.63 and validation accuracy is 16401/25000      65.6
training loss is  0.56 and training accuracy is 17777/25000     71.11
validation loss is  0.61 and validation accuracy is 16839/25000     67.36
training loss is  0.52 and training accuracy is 18497/25000     73.99
validation loss is  0.59 and validation accuracy is 17312/25000     69.25
training loss is  0.49 and training accuracy is 19128/25000     76.51
validation loss is  0.59 and validation accuracy is 17492/25000   

위 코드에서 데이터를 배치 처리하기 위해 만든 BucketIterator 객체들이 train_iter와 test_iter를 입력해 fit 함수를 호출한다.

또한 BucketIterator 객체의 기본 설정은 배치 생성을 중단하지 않는다.

따라서 학습을 시작하기 전에 BucketIterator 객체의 repeat 변수를 False로 설정해야만 한다.

repeat 변수를 False로 설정하지 않으면 fit 함수가 무기한으로 실행된다....